In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 10000 
args.init_model = "{}-attention-sink6-test8".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 1001
args.conn_lambda_epochs_end = 3000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 1001
args.valency_lambda_epochs_end = 3000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 1001
args.euler_lambda_epochs_end = 3000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 4000

args.cross_att_use = True
args.cross_att_random = False
args.cross_att_n_sinkhorn = 6
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=3000, conn_lambda_epochs_start=1001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=6, cross_att_random=False, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=3000, euler_lambda_epochs_start=1001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='deepsets-attention-sink6-test8_decode', init_model='deepsets-attention-sink6-test8', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=10000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_opt/output_dev4/

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

Found previous model mol_opt/output_dev4/deepsets-attention-sink6-test8/model_deepsets-attention-sink6-test8_1780, epoch 1780. Overwriting args.
Penalty params: tau=0.12891 conn_l=0.02268 val_l=0.02768 euler_l=0.01937 epoch=1780 mode=[1 1 1] conn=True val=True euler=True
Epoch: 1781


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:0.5338014
 conn_penalty:0.0307413
 val_penalty:1.7860982
 euler_penalty:1.2445129
 total:0.6080418
Penalty params: tau=0.12876 conn_l=0.02277 val_l=0.02780 euler_l=0.01944 epoch=1781 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.12876 conn_l=0.02277 val_l=0.02780 euler_l=0.01944 epoch=1781 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1781, train
 fgw:0.5338014
 conn_penalty:0.0307413
 val_penalty:1.7860982
 euler_penalty:1.2445129
 total:0.6080418
Epoch duration: 2.3636651039123535
Epoch: 1782
Losses Batch 0, train
 fgw:0.5439312
 conn_penalty:0.0057349
 val_penalty:3.0700143
 euler_penalty:3.5568021
 total:0.6985510
Penalty params: tau=0.12861 conn_l=0.02287 val_l=0.02792 euler_l=0.01951 epoch=1782 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.12861 conn_l=0.02287 val_l=0.02792 euler_l=0.01951 epoch=1782 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1782, train
 fgw:0.5439312
 conn_penalty:0.0057349


Losses Batch 0, train
 fgw:0.5279876
 conn_penalty:0.0091086
 val_penalty:1.2236346
 euler_penalty:0.4864462
 total:0.5742895
Penalty params: tau=0.12655 conn_l=0.02418 val_l=0.02964 euler_l=0.02058 epoch=1796 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.12655 conn_l=0.02418 val_l=0.02964 euler_l=0.02058 epoch=1796 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1796, train
 fgw:0.5279876
 conn_penalty:0.0091086
 val_penalty:1.2236346
 euler_penalty:0.4864462
 total:0.5742895
Epoch duration: 2.8594532012939453
Epoch: 1797
Losses Batch 0, train
 fgw:0.5299072
 conn_penalty:0.0145618
 val_penalty:1.4086021
 euler_penalty:0.6487505
 total:0.5853561
Penalty params: tau=0.12641 conn_l=0.02428 val_l=0.02976 euler_l=0.02066 epoch=1797 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.12641 conn_l=0.02428 val_l=0.02976 euler_l=0.02066 epoch=1797 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1797, train
 fgw:0.5299072
 conn_penalty:0.0145618


Losses Batch 0, train
 fgw:0.5216976
 conn_penalty:0.0166383
 val_penalty:1.1897121
 euler_penalty:0.4149131
 total:0.5685557
Penalty params: tau=0.12439 conn_l=0.02568 val_l=0.03159 euler_l=0.02179 epoch=1811 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.12439 conn_l=0.02568 val_l=0.03159 euler_l=0.02179 epoch=1811 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1811, train
 fgw:0.5216976
 conn_penalty:0.0166383
 val_penalty:1.1897121
 euler_penalty:0.4149131
 total:0.5685557
Epoch duration: 3.9216227531433105
Epoch: 1812
Losses Batch 0, train
 fgw:0.5211079
 conn_penalty:0.0147000
 val_penalty:1.1793157
 euler_penalty:0.4234315
 total:0.5679693
Penalty params: tau=0.12424 conn_l=0.02579 val_l=0.03173 euler_l=0.02187 epoch=1812 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.12424 conn_l=0.02579 val_l=0.03173 euler_l=0.02187 epoch=1812 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1812, train
 fgw:0.5211079
 conn_penalty:0.0147000


...

Losses Batch 0, train
 fgw:49.3805811
 conn_penalty:21.4413354
 val_penalty:17.3200000
 euler_penalty:7.0600000
 total:214.4245898
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10856 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10856 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10856, train
 fgw:49.3805811
 conn_penalty:21.4413354
 val_penalty:17.3200000
 euler_penalty:7.0600000
 total:214.4245898
Epoch duration: 3.452038526535034
Epoch: 10857
Losses Batch 0, train
 fgw:49.1472070
 conn_penalty:22.0508716
 val_penalty:17.0400000
 euler_penalty:6.7800000
 total:214.0598242
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10857 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10857 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10857, train
 fgw:49.1472070
 c

Losses Batch 0, train
 fgw:46.7066846
 conn_penalty:20.3250720
 val_penalty:16.7400000
 euler_penalty:6.4200000
 total:204.2218945
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10871 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10871 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10871, train
 fgw:46.7066846
 conn_penalty:20.3250720
 val_penalty:16.7400000
 euler_penalty:6.4200000
 total:204.2218945
Epoch duration: 3.4578516483306885
Epoch: 10872
Losses Batch 0, train
 fgw:46.5883008
 conn_penalty:20.7793555
 val_penalty:16.7400000
 euler_penalty:6.4600000
 total:205.5463672
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10872 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10872 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10872, train
 fgw:46.5883008
 

Losses Batch 0, train
 fgw:48.2278662
 conn_penalty:8.7633496
 val_penalty:22.2811108
 euler_penalty:15.3011157
 total:216.5257031
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10886 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10886 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10886, train
 fgw:48.2278662
 conn_penalty:8.7633496
 val_penalty:22.2811108
 euler_penalty:15.3011157
 total:216.5257031
Epoch duration: 3.8402888774871826
Epoch: 10887
Losses Batch 0, train
 fgw:48.2443750
 conn_penalty:10.1844739
 val_penalty:21.6975952
 euler_penalty:14.6642383
 total:216.6142578
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10887 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10887 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10887, train
 fgw:48.2443750


Saved at mol_opt/output_dev4/deepsets-attention-sink6-test8/model_deepsets-attention-sink6-test8_10900
Epoch: 10901
Losses Batch 0, train
 fgw:48.0422461
 conn_penalty:12.3283374
 val_penalty:20.1599158
 euler_penalty:10.9799158
 total:207.7866602
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10901 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10901 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10901, train
 fgw:48.0422461
 conn_penalty:12.3283374
 val_penalty:20.1599158
 euler_penalty:10.9799158
 total:207.7866602
Epoch duration: 3.6046314239501953
Epoch: 10902


KeyboardInterrupt: 